In [1]:
import random
import numpy as np
import operator
import pandas as pd
from datetime import datetime, timedelta
import pickle
import time

In [2]:
global total_utxo
global total_Address
global clusters

# Class

In [3]:
class utxo(object):
    def __init__(self, value, address):
        self.value = value
        self.address = address

class Address(object):
    def __init__(self, id, utxo_set, Node):
        self.id = id
        self.utxo_set = utxo_set
        self.Node = Node
    
    def balance(self):
        b = 0
        for utxo in self.utxo_set:
            b += utxo.value
        return b
    
    def get_utxo(self, new_utxo):
        self.utxo_set += [new_utxo]
        total_utxo.append(new_utxo)
        
    def spend_utxo(self, old_utxo):
        self.utxo_set.remove(old_utxo)
        total_utxo.remove(old_utxo)
        
    def utxo_num(self):
        return len(utxo_set)

class Node:
    def __init__(self,id):
        self.id = id
        self.address_set = []
        self.transactionsPool= []
    
    def generate_new_address(self, Address):
        a = Address
        self.address_set.append(a)
        total_Address.append(a)
        
    def get_utxo(self, utxo_value, gna = True):
        if gna:
            u = utxo(utxo_value, self.address_set[-1])
            self.address_set[-1].get_utxo(u)
        else:
            address_get = random.choice(self.address_set)
            address_get.get_utxo(utxo(utxo_value, address_get))
            
    def balance(self):
        b = 0
        for addr in self.address_set:
            b += addr.balance()
        return b
    
    def utxo_set(self):
        utxo_set = []
        for a in self.address_set:
            utxo_set += a.utxo_set
        return utxo_set
    
    def utxo_num(self):
        return len(self.utxo_set())
    
class Transaction(object):
    def __init__(self, id, type, sender, to, value):
        self.id = id
        self.type = type
        self.sender = sender
        self.to= to
        self.value=value
        
    def execute(self, GNA_bool):
        
        for spending_utxo in self.sender:
            spending_utxo.address.spend_utxo(spending_utxo)
            
        for i in range(len(self.to)):
            if GNA_bool[i] == True or self.to[i].address_set == []:
                a = Address(id = len(total_Address), utxo_set = [], Node = self.to[i])
                self.to[i].generate_new_address(a)
            else:
                a = random.choice(to[i].address_set)
            self.to[i].get_utxo(self.value[i], GNA_bool[i])
            
            
        if self.type == "peel":
            if len(self.sender) == 1:
                if self.sender[0].Node == self.to[1]:
                    c = Cluster(len(clusters), [self.sender[0].address, self.to[1].address_set[-1]])
                    clusters.append(c)
class Cluster(object):
    def __init__(self, id, address_set):
        self.id = id
        self.address_set = address_set
        
    def address_num(self):
        return len(self.address_set)    
    
    def cluster_sum(self, other_cluster):
        sas = set(self.address_set)
        ocas = set(other_cluster.address_set)
        if sas - ocas != sas:
            self.address_set = list(sas | ocas)
            clusters.remove(other_cluster)

# SilkRoad4 Setting

In [4]:
dx = pd.read_excel('../data/data.xlsx')
datar = []
for i in range(len(dx)):
    tmp = [dx["ID"][i], dx["Value"][i], dx["Date"][i]]
    ttmp = datetime.strptime(str(tmp[2]), "%Y%m%d")
    tmp[2] = ttmp
    datar.append(tmp)
    
#print(datar)
data = []
for v in datar:
    if v not in data:
        data.append(v)
data_t = []
for d in data:
    data_t.append(d[2])
start = min(data_t)
end = max(data_t)

r_data_index = np.random.choice(range(len(data)), 100, replace=False)
r_data = []
for r_index in r_data_index:
    data[r_index][1] = round(data[r_index][1]*pow(10,8))
    r_data.append(data[r_index])
r_data

review_index = []
for rd in r_data:
    time_difference = int((rd[2]-start).days)*5120
    if time_difference - 71680 < 0:
        time_range = range(time_difference)
    else:
        time_range = range(time_difference-71680, time_difference)
    random_time = random.choice(time_range)
    review_index.append(random_time)
print(review_index)

[413026, 375537, 252431, 228572, 351924, 150093, 373087, 37188, 641029, 272220, 149757, 298327, 195576, 200854, 165541, 602106, 271063, 151049, 359359, 462744, 543131, 627847, 224459, 306443, 167256, 343479, 560952, 448815, 249624, 83736, 250469, 142811, 516203, 196509, 270574, 392611, 3797, 457389, 361369, 550172, 297104, 309379, 249825, 288101, 304222, 467019, 183917, 229272, 548284, 530383, 397591, 420602, 454871, 345271, 250332, 518612, 207227, 234180, 533156, 450885, 469226, 578388, 93789, 607878, 263961, 298568, 111282, 566086, 196183, 525932, 534803, 260651, 153032, 267386, 500643, 83521, 75724, 442130, 327008, 327141, 70972, 58910, 453569, 263964, 342409, 135358, 470692, 578323, 554639, 374780, 374308, 274534, 206897, 364767, 127339, 214811, 233676, 236081, 370025, 318110]


# Transaction Setting

In [5]:
co_value = []

with open('co_value.txt', 'r') as filehandle:
    for line in filehandle:
        currentPlace = line[:-1]
        co_value.append(int(currentPlace))

with open("rov.pickle", "rb") as f:
    relay_tx_output_value = pickle.load(f)
rov = list(relay_tx_output_value)        
        
with open("pic.pickle", "rb") as f:
    peel_tx_input_count = pickle.load(f)
peel_tx_input_count = list(peel_tx_input_count)

with open("sov.pickle", "rb") as f:
    sweep_tx_output_value = pickle.load(f)
sov = list(sweep_tx_output_value)

with open("ptx1ov.pickle", "rb") as f:
    ptx1ov = pickle.load(f)
ptx1ov = list(ptx1ov)

with open("ptxov.pickle", "rb") as f:
    ptxov = pickle.load(f)
ptxov = list(ptxov)

with open("dtxov.pickle", "rb") as f:
    dtxov = pickle.load(f)
dtxov = list(dtxov)

with open("mtxic.pickle", "rb") as f:
    mic = pickle.load(f)
mic = list(mic)

with open("mtxov.pickle", "rb") as f:
    mtxov = pickle.load(f)
mtxov = list(mtxov)

with open("utxo.pickle", "rb") as f:
    past_utxo = pickle.load(f)
past_utxo = list(past_utxo)
utxos = np.random.choice(past_utxo, 160000)

In [6]:
def find_utxo(v):
    candidate_utxo = []
    utxo_difference = []
    for u in total_utxo:
        if u.value > v:
            candidate_utxo.append(u)
            utxo_difference.append(u.value - v)
    if utxo_difference == []:
        gun = np.random.choice(range(2,22000))
        a = Address(id = len(total_Address), utxo_set = [], Node = NODES[gun])
        NODES[gun].generate_new_address(a)
        NODES[gun].get_utxo(v + random.choice(range(21526)), gna = True)
        return NODES[gun].address_set[-1].utxo_set[0]
    return candidate_utxo[utxo_difference.index(min(utxo_difference))]

def find_utxos(n, fee_range, v):
    input_sum = 0
    inputs = np.random.choice(total_utxo, n, replace=False)
    while (input_sum - v) in fee_range:
        inputs = np.random.choice(total_utxo, n, replace=False)
        inputs_value = []
        for i in inputs:
            inputs_value.append(i.value)
        input_sum = sum(inputs_value)
    
    return inputs    

def find_Node(v):
    candidate_node = []
    value_difference = []
    for n in NODES:
        if n.balance() > v:
            candidate_node.append(n)
            value_difference.append(n.balance() - v)
    if value_difference == []:
        gun = np.random.choice(range(2,22000))
        a = Address(id = len(total_Address), utxo_set = [], Node = NODES[gun])
        NODES[gun].generate_new_address(a)
        NODES[gun].get_utxo(v + random.choice(range(21526)), gna = True)
        return NODES[gun].address_set[-1].utxo_set
    selected_Node = candidate_node[value_difference.index(min(value_difference))]
    selected_utxos = []
    for sa in selected_Node.address_set:
        selected_utxos += sa.utxo_set
    return selected_utxos

In [9]:
start = time.time()

pool=[]
total_utxo = []
total_Address = []
clusters = []

################################
NODES = []
print("Node start")
# SilkRoad escrow
NODES.append(Node(id=0))

# Miner
NODES.append(Node(id=1))
NODES.append(Node(id=2))

#UTXO from before
for i in range(3, 22000):
    NODES.append(Node(id=i))

#UTXO from after
for i in range(22001, 50000):
    NODES.append(Node(id=i))
    
for i in range(160000):
    gun = np.random.choice(range(3,22000))
    a = Address(id = len(total_Address), utxo_set = [], Node = NODES[gun])
    NODES[gun].generate_new_address(a)
    NODES[gun].get_utxo(int(utxos[i]), gna = True)
#####################################

print("Node end")

tx_type = ["mining", "relay", "peel", "distribution", "sweep", "mimo"]
bool_list = [True, False]
print("tx start")
for i in range(670000):
    if i % 1000 == 0:
        print(i)
    id = i
    review_flag = False
    if i in review_index:
        review_value = r_data[review_index.index(i)][1]
        review_flag = True
        type = np.random.choice(["relay", "peel", "distribution", "sweep", "mimo"], p=[0.125, 0.7005, 0.07, 0.07, 0.0345])
    else :
        type = np.random.choice(tx_type, 1, p=[0.0005, 0.125, 0.7, 0.07, 0.07, 0.0345])[0]
            
    ##################  MINING #####################################
    if type == "mining":
        sender = []
        to = [NODES[1]]
        GNA_bool = [np.random.choice(bool_list, p=[4/7, 3/7])]
        mining_reward = np.random.choice(co_value)
        co_value.remove(mining_reward)
        value = [mining_reward]
    ################################################################ => No Clustering
    
    ################# RELAY ########################################
    elif type == "relay":
        if review_flag == True:
            sender = [find_utxo(review_value)]
            to = [NODES[0]]
            GNA_bool = [True]
            value = [review_value]
        else :
            value = [random.choice(rov)]
            sender = [find_utxo(value[0])] 
            to = [random.choice(NODES)]
            GNA_bool = [np.random.choice(bool_list, p=[0.45, 0.55])]
    ################################################################# => No Clustering
    
    ############### PEEL ###########################################
    elif type == "peel":
        Input_one_bool = np.random.choice(bool_list, p=[0.77, 0.23])
        
        if Input_one_bool:
            if review_flag:
                not_find_flag = True
                for ptx1o in ptx1ov:
                    if review_value in ptx1o:
                        value = ptx1o
                        not_find_flag = False
                        break
                if not_find_flag:
                    value = random.choice(ptx1ov)
                    value[0] = review_value
                
                value_sum = sum(value)
                sender = [find_utxo(value_sum)]
                OTC_bool = np.random.choice(bool_list, p=[0.48, 0.52])
                if OTC_bool:
                    to = [NODES[0], sender[0].address.Node]
                    GNA_bool = [True, True]
                else : 
                    to = [NODES[0], random.choice(NODES)]
                    GNA_bool = [True, np.random.choice(bool_list, p=[0.45, 0.55])]
                
            else:
                value = random.choice(ptx1ov)
                value_sum = sum(value)
                sender = [find_utxo(value_sum)]
                
                OTC_bool = np.random.choice(bool_list, p=[0.48, 0.52])
                if OTC_bool:
                    to = [random.choice(NODES), sender[0].address.Node]
                    GNA_bool = [np.random.choice(bool_list, p=[0.45, 0.55]), True]
                else : 
                    to = [random.choice(NODES), random.choice(NODES)]
                    GNA_bool = np.random.choice(bool_list, 2, p=[0.45, 0.55])
                
        
        else:
            if review_flag:
                not_find_flag = True
                for ptxo in ptxov:
                    if review_value in ptxo:
                        not_find_flag = False
                        value = ptxo
                        break
                if not_find_flag:
                    value = random.choice(ptx1ov)
                    value[0] = review_value
    
                value_sum = sum(value)
                tic = random.choice(peel_tx_input_count)
                peel_tx_input_count.remove(tic)
                fee_range = range(21526)
                sender = find_utxos(tic, fee_range, value_sum)
                to = [NODES[0], random.choice(NODES)]
                GNA_bool = [True, np.random.choice(bool_list, p=[0.45, 0.55])]
            else :
                value = random.choice(ptxov)
                value_sum = sum(value)
                tic = random.choice(peel_tx_input_count)
                peel_tx_input_count.remove(tic)
                fee_range = range(21526)
                sender = find_utxos(tic, fee_range, value_sum)
                to = [random.choice(NODES), random.choice(NODES)]
                GNA_bool = np.random.choice(bool_list, 2, p=[0.45, 0.55])
 
    ################################################################ => Clustering

    ######################      DT     #############################
    elif type == "distribution":
        if review_flag:
            not_find_flag = True
            for dtxovlist in dtxov:
                if review_value in dtxovlist:
                    value = dtxovlist
                    not_find_flag = False
                    break
            if not_find_flag:
                value = random.choice(dtxov)
                value.append(review_value)
            oc = len(value)
            value_sum = sum(value)
            sender = [find_utxo(value_sum)]

            to = np.random.choice(NODES, oc)
            to[value.index(review_value)] = NODES[0]
            GNA_bool = np.random.choice(bool_list, oc, p=[0.52,0.48])
            GNA_bool[value.index(review_value)] = True
        else:
            value = random.choice(dtxov)
            oc = len(value)
            value_sum = sum(value)
            sender = [find_utxo(value_sum)]

            to = np.random.choice(NODES, oc)
            GNA_bool = np.random.choice(bool_list, oc, p=[0.52,0.48])
    ################################################################# => No Clustering
    
    ####################  SWEEP ####################################
    elif type == "sweep":
        if review_flag:
            value = [review_value]
            to = [NODES[0]]
        else:
            value = [random.choice(sov)]
            sov.remove(value[0])
            to = [random.choice(NODES)]
        
        sender = find_Node(value[0])
        GNA_bool = [np.random.choice(bool_list, p=[0.41, 0.59])]
        
        if len(sender) > 1:
            sa = []
            for su in sender:
                sa.append(su.address)
        
        c = Cluster(len(clusters), sa)
        clusters.append(c)
    ################################################################# => Clustering
    
    ##################### MIMO ##############################
    else:
        if review_flag:
            not_find_flag = True
            for mtxo in mtxov:
                if review_value in mtxo:
                    not_find_flag = False
                    value = mtxo
                    break
            if not_find_flag:
                value = np.random.choice(mtxov)
                value.append(review_flag)
            value_sum = sum(value) 
            
            ic = np.random.choice(mic)
            mic.remove(ic)
            
            fee_range = range(110415)
            sender = find_utxos(ic, fee_range, value_sum)
            
            oc = len(value)

            to = np.random.choice(NODES, oc)
            to[value.index(review_value)] = NODES[0]
            GNA_bool = np.random.choice(bool_list, oc, p=[0.41, 0.59])
            GNA_bool[value.index(review_value)] = True
        else:
            value = np.random.choice(mtxov)
            value_sum = sum(value)
            
            ic = np.random.choice(mic)
            mic.remove(ic)
            
            fee_range = range(110415)
            sender = find_utxos(ic, fee_range, value_sum)
            
            oc = len(value)

            to = np.random.choice(NODES, oc)
            GNA_bool = np.random.choice(bool_list, oc, p=[0.41, 0.59])

    ################################################################## => No Clustering
    
    tx = Transaction(id, type, sender, to, value)
    tx.execute(GNA_bool) 
    pool += [tx] #-> Matching
    
print("time :", (time.time() - start)/60)

Node start
Node end
tx start
0


/home/isslab/.local/lib/python3.6/site-packages/ipykernel_launcher.py:224: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray


1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000
15

In [10]:
for c in clusters:
    print(clusters.index(c))
    print("before : " , c.address_num())
    for i in range(clusters.index(c)+1, len(clusters)):
        if i >= len(clusters):
            break
        c.cluster_sum(clusters[i])
    print("after : ", c.address_num())

0
before :  2
after :  2
1
before :  3
after :  3
2
before :  3
after :  3
3
before :  4
after :  4
4
before :  4
after :  4
5
before :  16
after :  23
6
before :  3
after :  3
7
before :  8
after :  10
8
before :  4
after :  4
9
before :  8
after :  9
10
before :  4
after :  4
11
before :  6
after :  8
12
before :  5
after :  5
13
before :  12
after :  12
14
before :  11
after :  22
15
before :  5
after :  5
16
before :  6
after :  6
17
before :  6
after :  8
18
before :  5
after :  9
19
before :  10
after :  10
20
before :  3
after :  7
21
before :  4
after :  9
22
before :  5
after :  5
23
before :  6
after :  6
24
before :  8
after :  8
25
before :  6
after :  6
26
before :  3
after :  7
27
before :  7
after :  7
28
before :  11
after :  11
29
before :  6
after :  6
30
before :  9
after :  9
31
before :  5
after :  5
32
before :  3
after :  3
33
before :  8
after :  8
34
before :  6
after :  6
35
before :  8
after :  13
36
before :  5
after :  5
37
before :  6
after :  6
38
before 

after :  12
305
before :  5
after :  10
306
before :  8
after :  8
307
before :  8
after :  8
308
before :  7
after :  17
309
before :  14
after :  18
310
before :  7
after :  7
311
before :  6
after :  6
312
before :  6
after :  6
313
before :  12
after :  12
314
before :  5
after :  5
315
before :  3
after :  3
316
before :  2
after :  2
317
before :  7
after :  7
318
before :  9
after :  12
319
before :  5
after :  7
320
before :  5
after :  5
321
before :  6
after :  6
322
before :  3
after :  3
323
before :  6
after :  14
324
before :  10
after :  10
325
before :  4
after :  15
326
before :  5
after :  5
327
before :  7
after :  12
328
before :  6
after :  6
329
before :  5
after :  5
330
before :  5
after :  5
331
before :  3
after :  3
332
before :  8
after :  8
333
before :  9
after :  9
334
before :  8
after :  8
335
before :  7
after :  7
336
before :  6
after :  6
337
before :  8
after :  14
338
before :  9
after :  16
339
before :  14
after :  14
340
before :  10
after :  1

after :  5
605
before :  3
after :  3
606
before :  9
after :  9
607
before :  3
after :  3
608
before :  8
after :  8
609
before :  5
after :  5
610
before :  2
after :  2
611
before :  2
after :  2
612
before :  6
after :  6
613
before :  5
after :  5
614
before :  11
after :  13
615
before :  6
after :  4
616
before :  7
after :  7
617
before :  7
after :  7
618
before :  8
after :  8
619
before :  2
after :  11
620
before :  7
after :  7
621
before :  2
after :  2
622
before :  10
after :  22
623
before :  2
after :  2
624
before :  4
after :  4
625
before :  2
after :  3
626
before :  7
after :  11
627
before :  9
after :  9
628
before :  7
after :  6
629
before :  7
after :  7
630
before :  6
after :  6
631
before :  10
after :  10
632
before :  9
after :  9
633
before :  6
after :  19
634
before :  5
after :  8
635
before :  12
after :  16
636
before :  10
after :  10
637
before :  3
after :  4
638
before :  5
after :  15
639
before :  2
after :  2
640
before :  8
after :  8
641

after :  8
907
before :  12
after :  17
908
before :  5
after :  5
909
before :  9
after :  10
910
before :  7
after :  5
911
before :  6
after :  13
912
before :  6
after :  6
913
before :  6
after :  6
914
before :  2
after :  6
915
before :  2
after :  2
916
before :  6
after :  6
917
before :  8
after :  8
918
before :  4
after :  20
919
before :  4
after :  17
920
before :  2
after :  2
921
before :  9
after :  11
922
before :  9
after :  14
923
before :  6
after :  6
924
before :  10
after :  10
925
before :  5
after :  8
926
before :  2
after :  1
927
before :  2
after :  2
928
before :  8
after :  13
929
before :  9
after :  10
930
before :  5
after :  5
931
before :  2
after :  2
932
before :  2
after :  1
933
before :  3
after :  3
934
before :  12
after :  12
935
before :  8
after :  8
936
before :  3
after :  7
937
before :  4
after :  16
938
before :  4
after :  10
939
before :  12
after :  12
940
before :  8
after :  13
941
before :  2
after :  1
942
before :  6
after :  

after :  4
1201
before :  5
after :  5
1202
before :  6
after :  12
1203
before :  6
after :  6
1204
before :  3
after :  3
1205
before :  8
after :  8
1206
before :  14
after :  14
1207
before :  5
after :  5
1208
before :  11
after :  11
1209
before :  11
after :  11
1210
before :  4
after :  4
1211
before :  7
after :  6
1212
before :  2
after :  2
1213
before :  3
after :  3
1214
before :  11
after :  11
1215
before :  9
after :  14
1216
before :  8
after :  12
1217
before :  5
after :  5
1218
before :  9
after :  9
1219
before :  9
after :  13
1220
before :  9
after :  9
1221
before :  6
after :  6
1222
before :  9
after :  13
1223
before :  3
after :  2
1224
before :  4
after :  10
1225
before :  2
after :  2
1226
before :  6
after :  5
1227
before :  6
after :  6
1228
before :  2
after :  19
1229
before :  2
after :  2
1230
before :  2
after :  14
1231
before :  6
after :  5
1232
before :  6
after :  6
1233
before :  5
after :  5
1234
before :  2
after :  2
1235
before :  2
afte

...

after :  2
31629
before :  8
after :  6
31630
before :  5
after :  5
31631
before :  12
after :  12
31632
before :  12
after :  12
31633
before :  13
after :  11
31634
before :  3
after :  3
31635
before :  8
after :  8
31636
before :  14
after :  14
31637
before :  2
after :  2
31638
before :  11
after :  11
31639
before :  10
after :  10
31640
before :  10
after :  10
31641
before :  10
after :  10
31642
before :  8
after :  8
31643
before :  7
after :  7
31644
before :  15
after :  12
31645
before :  9
after :  9
31646
before :  11
after :  11
31647
before :  2
after :  2
31648
before :  8
after :  7
31649
before :  8
after :  8
31650
before :  6
after :  6
31651
before :  11
after :  11
31652
before :  2
after :  2
31653
before :  14
after :  14
31654
before :  2
after :  2
31655
before :  13
after :  9
31656
before :  13
after :  13
31657
before :  13
after :  11
31658
before :  12
after :  12
31659
before :  5
after :  5
31660
before :  4
after :  4
31661
before :  2
after :  2
3

after :  9
31907
before :  4
after :  4
31908
before :  3
after :  3
31909
before :  18
after :  18
31910
before :  7
after :  7
31911
before :  3
after :  3
31912
before :  15
after :  15
31913
before :  7
after :  7
31914
before :  4
after :  4
31915
before :  16
after :  16
31916
before :  9
after :  6
31917
before :  9
after :  9
31918
before :  2
after :  2
31919
before :  8
after :  8
31920
before :  4
after :  4
31921
before :  10
after :  10
31922
before :  5
after :  5
31923
before :  2
after :  2
31924
before :  10
after :  10
31925
before :  8
after :  8
31926
before :  9
after :  9
31927
before :  2
after :  2
31928
before :  8
after :  8
31929
before :  10
after :  10
31930
before :  5
after :  5
31931
before :  8
after :  7
31932
before :  8
after :  8
31933
before :  7
after :  6
31934
before :  14
after :  14
31935
before :  7
after :  7
31936
before :  4
after :  4
31937
before :  2
after :  2
31938
before :  13
after :  13
31939
before :  10
after :  10
31940
before :

after :  2
32268
before :  8
after :  8
32269
before :  7
after :  7
32270
before :  7
after :  7
32271
before :  14
after :  14
32272
before :  5
after :  5
32273
before :  2
after :  2
32274
before :  2
after :  2
32275
before :  10
after :  10
32276
before :  2
after :  2
32277
before :  8
after :  7
32278
before :  4
after :  4
32279
before :  8
after :  8
32280
before :  2
after :  2
32281
before :  5
after :  5
32282
before :  3
after :  3
32283
before :  9
after :  9
32284
before :  12
after :  10
32285
before :  9
after :  9
32286
before :  10
after :  10
32287
before :  6
after :  6
32288
before :  3
after :  3
32289
before :  2
after :  2
32290
before :  5
after :  4
32291
before :  5
after :  5
32292
before :  2
after :  2
32293
before :  6
after :  6
32294
before :  9
after :  9
32295
before :  8
after :  8
32296
before :  10
after :  10
32297
before :  2
after :  2
32298
before :  12
after :  12
32299
before :  2
after :  2
32300
before :  3
after :  3
32301
before :  8
af

before :  4
after :  4
32607
before :  5
after :  5
32608
before :  10
after :  8
32609
before :  9
after :  9
32610
before :  9
after :  9
32611
before :  3
after :  3
32612
before :  3
after :  3
32613
before :  15
after :  15
32614
before :  4
after :  4
32615
before :  6
after :  6
32616
before :  7
after :  7
32617
before :  13
after :  13
32618
before :  2
after :  2
32619
before :  3
after :  3
32620
before :  7
after :  7
32621
before :  5
after :  5
32622
before :  2
after :  2
32623
before :  6
after :  6
32624
before :  2
after :  2
32625
before :  9
after :  9
32626
before :  2
after :  2
32627
before :  17
after :  17
32628
before :  8
after :  8
32629
before :  18
after :  18
32630
before :  14
after :  14
32631
before :  12
after :  12
32632
before :  4
after :  4
32633
before :  4
after :  4
32634
before :  8
after :  8
32635
before :  11
after :  11
32636
before :  5
after :  5
32637
before :  9
after :  9
32638
before :  2
after :  2
32639
before :  10
after :  10
326

33006
before :  10
after :  10
33007
before :  5
after :  5
33008
before :  5
after :  5
33009
before :  13
after :  13
33010
before :  7
after :  5
33011
before :  7
after :  7
33012
before :  8
after :  8
33013
before :  2
after :  2
33014
before :  12
after :  12
33015
before :  13
after :  11
33016
before :  17
after :  17
33017
before :  3
after :  3
33018
before :  11
after :  8
33019
before :  11
after :  11
33020
before :  3
after :  3
33021
before :  3
after :  3
33022
before :  5
after :  5


In [102]:
match = 0
for rd in r_data:
    count = 0
    rd_d = int((rd[2]-min(data_t)).days)*5120
    for t in pool:
        if t.id > rd_d:
            break
        if rd[1] in t.value:
            count += 1
            tid = t.id
    if count == 1:
        if tid == review_index[r_data.index(rd)]:
            match += 1
        #print(rd)
        #print(tid)
        
print(match)

31


In [103]:
match = 0
for rd in r_data:
    count = 0
    #rd_d = int((rd[2]-min(data_t)).days)*5120
    for t in pool:
        #if t.id > rd_d:
        #    break
        if rd[1] in t.value:
            count += 1
            #tid = t.id
    if count == 0:
        #if tid == review_index[r_data.index(rd)]:
        match += 1
        #print(rd)
        #print(tid)
        
print(match)

0


In [101]:
match = []
for rd in r_data:
    print(rd)
    count = []
    
    time_difference = int((rd[2]-min(data_t)).days)*5120
    time_range = range(time_difference)
        
    for t in pool[time_range[0]:time_range[-1]]:
        if rd[1] in t.value:
            for t2 in pool[time_range[-1]:]:
                for t2s in t2.sender:
                    if t2s.value == rd[1]:
                        if t2s.address.Node == NODES[0]:
                            count.append(t)
                            break
                            
    if len(count) == 1:
        if pool.index(count[0]) == review_index[r_data.index(rd)]:
            match.append(count[0])
        #print(rd)
        #print(tid)
    #break
print(len(match))

['deemtea', 2120500, datetime.datetime(2020, 7, 31, 0, 0)]
['CHINA77', 1966800, datetime.datetime(2020, 7, 31, 0, 0)]
['2chlor1', 2863700, datetime.datetime(2020, 7, 2, 0, 0)]
['halfway', 838600, datetime.datetime(2020, 6, 30, 0, 0)]
['widdak87', 806000, datetime.datetime(2020, 7, 24, 0, 0)]
['spanky04', 813100, datetime.datetime(2020, 6, 14, 0, 0)]
['onlineweb499900', 1870900, datetime.datetime(2020, 7, 22, 0, 0)]
['TazzGoSpazz1', 22500, datetime.datetime(2020, 5, 26, 0, 0)]
['Melon', 3208700, datetime.datetime(2020, 9, 14, 0, 0)]
['98calc', 5151600, datetime.datetime(2020, 7, 11, 0, 0)]
['zooyork097', 819500, datetime.datetime(2020, 6, 18, 0, 0)]
['cyfka7', 22100, datetime.datetime(2020, 7, 7, 0, 0)]
['randyjorgenson', 4233100, datetime.datetime(2020, 6, 22, 0, 0)]
['Johnnybegood420', 21500, datetime.datetime(2020, 6, 20, 0, 0)]
['bob46484648', 568100, datetime.datetime(2020, 6, 22, 0, 0)]
['Jjblaze148', 591000, datetime.datetime(2020, 9, 6, 0, 0)]
['Liquidswords66501', 22100, dateti

In [97]:
for t in match:
    print(NODES[0] in t.to)

True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


In [43]:
len(NODES[0].address_set)

125

In [28]:
len(clusters)

33023

In [31]:
cn = 0
for c in clusters:
    ca = c.address_set
    #print(len(ca))
    #print(len(list(set(ca))))
    if len(ca) != len(list(set(ca)-set(NODES[0].address_set))):
        cn+=1
print(cn)

2
2
3
3
3
3
4
4
4
4
23
23
3
3
10
10
4
4
9
9
4
4
8
8
5
5
12
12
22
22
5
5
6
6
8
8
9
9
10
10
7
7
9
9
5
5
6
6
8
8
6
6
7
7
7
7
11
11
6
6
9
9
5
5
3
3
8
8
6
6
13
13
5
5
6
6
3
3
5
5
19
19
3
3
12
12
11
11
12
12
5
5
11
11
7
7
3
3
2
2
6
6
2
2
16
16
2
2
11
11
6
6
4
4
3
3
15
15
6
6
8
8
5
5
3
3
14
14
3
3
7
7
17
17
10
10
8
8
8
8
6
6
6
6
3
3
7
7
9
9
9
9
15
15
9
9
11
11
4
4
12
12
7
7
3
3
8
8
3
3
6
6
10
10
13
13
3
3
7
7
6
6
16
16
18
18
11
11
11
11
6
6
2
2
8
8
7
7
4
4
19
19
4
4
8
8
3
3
8
8
2
1
4
4
4
4
10
10
7
7
10
10
7
7
15
15
8
8
7
7
17
17
7
6
5
5
2
2
8
8
5
5
7
7
9
9
8
8
10
10
10
10
2
2
8
8
7
7
6
6
17
17
6
6
7
7
7
7
7
6
4
4
3
3
11
11
6
6
10
10
5
4
17
17
9
9
12
12
9
9
7
7
13
13
14
14
2
2
13
13
7
7
9
9
8
8
10
10
10
10
5
5
5
4
5
5
7
7
13
13
7
7
9
9
9
9
7
7
11
11
2
2
4
4
6
6
13
13
17
17
11
11
13
13
6
6
6
6
4
4
3
3
3
3
13
13
5
5
6
6
15
15
7
7
6
6
12
12
11
10
4
4
5
5
7
7
16
16
16
16
6
6
2
2
10
10
8
8
8
8
7
7
9
9
12
12
7
7
7
7
4
4
6
6
16
16
3
3
3
3
7
7
9
9
5
5
6
6
10
10
11
11
7
7
11
11
9
9
8
8
13
13
17
17
5
5


3
11
11
12
12
7
7
7
7
4
4
2
2
4
2
4
4
2
2
3
3
7
7
7
7
2
2
2
2
7
7
4
4
8
8
5
4
6
6
3
2
1
1
10
10
14
14
4
4
1
1
2
1
10
10
5
5
1
1
11
11
10
10
17
17
5
5
12
12
3
3
3
3
3
3
2
2
2
2
7
6
14
14
6
6
4
4
7
7
7
7
4
2
3
3
9
9
6
6
4
4
5
4
1
1
15
12
2
1
14
14
2
2
7
7
8
8
4
4
5
5
3
3
5
5
5
5
2
2
2
1
4
2
4
2
6
6
3
2
2
2
7
7
6
6
8
7
9
9
6
6
12
12
2
1
8
8
5
5
3
3
2
1
14
14
2
1
2
2
8
8
5
4
3
3
2
2
9
7
9
9
3
2
9
9
3
2
7
7
16
16
11
10
2
2
2
1
12
12
10
10
13
13
2
2
14
14
11
11
10
8
7
7
18
18
10
10
11
10
5
5
4
2
2
2
2
2
7
6
6
6
6
6
4
4
7
6
2
1
6
6
12
12
6
6
2
1
3
3
5
5
10
10
4
3
8
8
5
4
2
2
15
15
3
3
3
2
10
10
7
7
8
8
15
15
10
10
9
9
4
4
11
11
9
8
2
2
11
8
2
2
2
2
10
10
3
3
5
5
3
2
2
2
2
2
13
13
2
2
2
1
1
1
2
1
8
6
9
9
3
3
9
8
2
2
12
12
2
2
6
5
7
7
3
2
14
14
5
5
2
2
6
6
3
2
2
1
2
2
4
4
8
8
2
1
3
3
14
14
7
7
9
9
12
12
3
2
7
7
2
2
6
6
4
4
2
2
1
1
10
10
4
3
2
2
4
4
5
4
3
1
5
5
4
2
2
2
2
2
10
10
14
14
4
4
2
1
2
2
1
1
6
6
11
10
7
7
4
4
6
6
11
11
9
9
6
5
2
2
3
2
5
4
10
10
7
7
2
2
2
2
3
3
7
5
8
8
15
15
3
3
8
6
9
9


4
3
8
8
8
8
6
6
4
2
11
11
7
7
17
17
6
6
3
3
7
7
3
2
9
8
6
6
9
9
5
4
12
12
3
2
3
3
2
2
3
3
6
5
6
6
4
4
3
2
8
8
4
3
6
6
11
11
3
2
2
2
3
2
2
2
3
3
6
6
2
2
2
2
2
2
3
2
4
1
5
4
2
2
2
2
21
21
14
13
1
1
2
1
5
5
3
2
2
2
4
4
5
5
9
9
4
2
2
2
4
3
5
5
2
1
21
21
7
7
3
2
2
2
7
7
7
7
2
2
2
1
4
3
4
3
7
5
5
5
9
9
3
2
3
2
5
5
8
8
3
1
7
6
6
6
7
3
8
5
4
3
13
12
4
4
10
8
5
5
6
5
6
6
7
7
8
8
10
10
7
6
3
3
6
2
8
5
6
6
8
7
4
4
4
2
9
9
7
7
2
2
12
12
2
2
6
6
6
6
12
12
5
4
10
10
4
4
2
2
2
2
9
9
10
10
4
4
2
2
4
4
4
4
3
2
7
6
3
2
3
3
5
5
3
3
6
3
7
5
2
2
2
2
8
8
4
4
3
2
6
6
2
2
8
8
6
6
12
12
5
1
6
5
10
10
5
5
4
4
7
4
2
1
3
3
6
6
12
12
5
5
2
2
2
2
4
1
13
13
3
2
2
2
2
2
11
11
5
2
6
6
7
6
3
3
13
13
1
1
4
4
3
3
8
7
8
7
8
7
3
2
6
4
1
1
3
1
6
5
1
1
3
3
5
5
7
5
2
2
12
12
4
4
6
5
9
9
2
2
5
3
5
4
5
5
6
6
8
8
5
4
14
14
9
9
11
11
2
2
7
6
6
6
2
2
3
2
6
5
4
4
4
3
3
1
5
4
6
6
2
2
1
1
4
4
10
10
6
6
3
2
5
2
2
2
10
8
3
3
10
9
15
15
9
9
5
4
4
3
4
2
3
3
9
8
5
5
9
7
11
11
9
9
5
3
8
8
10
9
2
1
2
1
11
11
6
4
2
2
8
8
3
3
3
2
15
15
7
4
4


7
6
5
5
9
9
6
4
6
6
2
2
3
3
9
8
2
2
12
12
2
2
2
2
6
6
2
2
3
3
5
3
4
4
4
3
5
5
2
2
6
6
2
2
2
2
4
4
3
3
5
1
5
3
8
8
7
7
5
5
3
3
4
4
8
8
3
3
4
4
3
3
7
7
5
3
3
3
4
4
3
1
5
4
2
1
6
6
4
4
10
8
8
8
7
7
3
3
7
6
4
4
12
12
6
6
4
2
13
13
2
2
3
2
5
4
2
1
3
1
3
3
9
9
7
7
2
1
12
10
6
6
13
13
5
3
8
8
4
3
4
3
7
5
6
6
2
2
4
4
5
5
10
10
2
2
4
3
3
2
10
10
13
13
4
3
7
5
3
3
6
6
4
2
7
7
5
2
2
1
6
6
9
7
3
3
3
3
4
4
3
2
5
4
7
7
3
3
11
11
2
2
4
3
11
11
4
4
3
2
11
11
9
9
6
3
6
4
3
3
4
3
3
3
17
17
3
3
4
2
4
4
3
2
6
4
3
3
4
3
3
3
4
4
3
2
4
4
5
5
6
6
3
3
6
6
5
5
2
2
2
2
9
9
7
7
4
4
5
3
8
7
2
1
4
2
12
12
3
3
3
3
10
10
5
4
4
4
3
3
6
5
10
9
5
5
4
4
3
2
2
1
2
1
3
3
3
2
2
2
5
4
7
7
3
3
6
6
7
5
4
4
3
3
2
2
5
3
4
4
3
2
6
5
3
1
3
1
8
8
2
2
7
6
6
4
4
4
7
5
7
6
4
4
3
2
3
3
2
2
3
2
7
7
2
2
21
21
7
7
10
10
6
5
2
1
2
2
2
2
3
3
2
2
8
8
4
4
4
3
3
3
3
2
2
1
6
5
8
8
7
7
7
7
9
9
8
8
12
12
3
3
8
8
6
5
3
2
2
2
5
3
6
5
4
4
4
4
3
3
6
4
6
5
9
9
9
9
9
6
2
2
5
5
2
2
5
3
6
6
4
3
8
8
3
3
11
11
8
6
2
2
6
6
17
17
4
4
5
3
17
17
11
11
2
2
4
4


3
8
8
7
7
15
15
3
3
3
3
5
5
13
13
6
5
4
3
3
3
8
6
3
3
4
3
5
5
3
3
5
4
5
4
6
4
9
8
3
3
3
3
5
5
4
3
9
9
5
5
6
3
11
8
6
6
6
6
7
6
9
6
4
4
7
7
6
5
3
3
3
2
4
4
10
10
7
4
5
5
6
6
7
7
8
7
6
6
5
4
9
7
10
10
4
4
3
2
3
3
3
3
2
2
8
8
2
2
3
3
6
6
11
11
2
1
10
10
9
7
2
1
4
2
4
4
10
10
6
4
4
2
10
10
5
4
2
2
5
5
2
2
8
8
11
11
10
10
5
4
12
12
9
9
2
2
4
4
8
8
9
9
5
4
3
2
10
10
8
8
5
5
5
5
10
10
10
10
5
5
7
7
6
6
6
5
6
6
13
13
7
6
6
4
7
7
3
3
16
16
4
3
8
8
4
4
7
4
4
3
14
14
5
5
3
3
9
6
6
5
4
4
6
5
9
8
3
3
5
5
5
4
6
5
7
5
6
5
6
5
2
1
4
4
11
9
3
3
3
3
5
2
2
1
3
3
10
8
6
6
9
9
2
2
6
6
4
2
8
8
1
1
5
4
5
5
6
4
5
3
10
8
2
2
3
3
4
4
3
2
7
7
8
7
3
3
14
14
8
8
2
2
3
2
7
7
8
7
5
5
5
5
4
4
6
6
6
5
10
10
2
2
2
2
9
5
8
8
8
8
4
4
2
2
5
5
9
7
4
4
4
4
13
13
4
4
9
9
5
4
9
9
5
3
5
2
7
7
2
2
6
6
10
5
9
4
4
4
4
4
5
4
6
4
4
3
8
8
10
10
4
4
13
13
8
8
5
5
5
5
7
7
2
2
8
4
7
7
6
3
11
11
8
7
6
6
10
10
5
4
3
2
4
4
9
9
2
2
14
14
6
6
5
5
11
11
7
7
13
10
1
1
4
2
10
10
11
9
6
6
5
3
3
3
1
1
4
4
13
13
11
11
3
3
7
7
5
5
11
8
5
5
11
11
3

...

5
9
7
9
9
9
5
7
6
7
5
2
2
3
3
13
13
3
3
4
4
4
4
5
5
7
6
2
2
2
1
6
6
6
6
13
13
6
6
6
4
6
4
14
14
5
5
5
4
7
6
13
12
10
5
2
2
9
9
10
10
10
9
5
5
6
3
6
6
3
3
2
2
3
3
1
1
8
8
9
9
10
10
7
7
15
15
10
10
10
7
4
4
3
2
3
3
3
3
9
8
5
5
2
2
6
5
7
6
7
7
7
7
12
12
9
7
10
10
2
2
3
3
5
5
10
7
5
5
7
7
2
2
8
8
13
13
12
12
3
3
5
5
11
7
3
3
9
8
7
7
4
4
6
5
2
2
4
4
7
7
7
7
9
9
11
9
5
3
6
6
12
10
8
7
8
8
6
6
8
8
3
2
6
6
13
13
2
2
11
11
4
4
3
3
2
2
8
5
6
6
4
4
4
3
7
7
11
11
17
17
5
5
4
3
8
8
6
5
8
7
10
10
7
5
8
8
5
5
6
5
3
3
3
3
10
7
14
14
6
6
8
4
17
13
7
7
12
12
4
4
11
11
11
11
12
12
3
3
3
3
4
4
4
4
14
14
3
3
5
5
4
4
9
7
10
10
4
4
5
5
12
12
14
11
4
4
3
2
6
6
7
7
4
3
9
9
9
9
4
3
2
2
3
3
2
2
11
11
3
3
11
11
2
2
2
2
8
6
7
7
15
14
12
12
5
5
5
5
9
7
8
8
7
4
11
11
6
6
9
9
6
6
5
5
4
4
8
8
9
9
9
9
9
8
9
9
7
7
10
10
7
6
10
7
9
9
8
8
4
4
9
7
9
7
11
8
6
6
7
7
4
2
12
12
9
9
5
5
7
7
6
6
5
4
9
8
4
4
2
2
5
5
5
5
13
13
11
10
8
7
8
8
4
4
11
10
2
2
9
9
9
8
13
13
2
2
9
9
3
3
11
11
4
4
3
3
4
4
10
10
10
8
4
4
5
5
2
2
2
2
5
5
11

11
9
9
8
2
2
7
6
7
5
13
12
12
9
5
3
10
10
10
8
2
2
8
8
7
7
13
12
9
9
6
6
5
5
9
4
8
8
9
9
11
11
3
2
6
4
7
7
3
3
3
3
2
2
5
5
4
4
3
3
6
6
4
4
8
7
6
6
8
6
6
6
6
6
8
8
2
2
4
4
6
6
16
16
5
4
3
3
4
3
11
9
13
11
2
2
2
2
2
2
8
8
3
3
5
5
6
6
5
5
2
2
7
6
11
11
6
6
7
6
6
5
2
2
2
2
9
9
10
9
6
6
9
9
7
7
7
6
6
5
3
3
3
3
7
7
10
10
5
5
8
8
9
6
7
7
2
2
2
2
10
8
2
2
3
3
10
10
7
6
10
8
5
5
3
3
4
4
4
4
8
8
2
2
9
9
11
10
9
7
7
7
9
9
6
6
2
2
8
7
8
8
4
4
2
2
11
11
5
5
4
4
2
2
11
10
5
5
9
8
9
9
7
6
9
9
9
6
7
7
9
7
11
10
5
3
3
3
4
3
6
4
10
8
2
2
8
6
9
8
3
3
16
15
4
4
8
8
5
5
5
5
3
3
5
3
5
5
4
4
10
10
7
7
2
2
9
7
5
4
2
2
4
4
2
2
10
10
8
8
12
12
9
5
2
2
7
7
6
6
7
6
9
8
5
5
6
6
2
2
9
8
2
2
15
15
11
8
3
3
9
7
7
7
9
6
5
5
4
4
7
6
3
2
11
9
9
8
4
4
3
3
4
4
5
5
9
7
9
9
3
3
8
8
8
8
4
4
6
5
11
8
13
13
2
2
11
11
9
9
10
9
9
9
2
2
9
9
7
7
4
4
2
2
2
2
5
5
9
9
11
10
10
8
7
7
3
3
8
6
8
8
12
12
7
7
6
6
3
3
8
7
13
13
8
8
3
3
9
8
2
2
12
12
2
2
11
11
6
5
10
8
4
4
7
7
8
7
3
2
2
2
6
6
8
6
10
10
11
8
10
7
12
7
9
8
8
8
9
7
2
2
4
4
6
5

5
4
2
2
3
3
10
9
7
7
10
8
3
3
11
9
3
2
9
8
3
3
7
7
6
6
12
12
8
8
2
2
5
4
5
4
8
8
15
13
8
7
14
14
4
4
5
4
6
6
2
2
2
2
5
4
15
11
10
10
2
2
10
9
10
10
5
5
10
9
8
7
9
9
3
3
4
4
9
8
2
2
8
5
6
6
11
9
8
8
9
7
7
7
12
10
4
4
17
16
2
2
6
6
7
5
15
14
2
2
8
6
8
8
3
3
6
6
13
11
3
3
2
2
7
7
7
6
6
6
6
6
20
17
7
6
2
2
3
3
17
13
14
13
8
7
10
10
13
13
8
6
10
10
11
10
12
9
5
5
4
4
7
7
6
6
7
7
7
7
14
8
1
1
2
1
4
4
6
6
2
2
17
16
5
5
10
10
4
4
3
3
9
8
8
8
4
4
11
10
9
6
7
6
8
7
5
5
7
7
3
2
2
2
10
6
7
7
2
2
4
4
2
2
2
2
13
12
12
12
2
2
7
7
9
7
7
6
6
6
7
7
8
8
6
6
5
3
5
5
7
7
3
3
5
5
8
8
6
6
9
8
2
2
10
9
11
11
4
4
5
5
8
7
6
6
4
4
7
7
3
2
6
6
7
7
6
5
3
3
13
13
9
9
5
5
11
8
8
8
7
7
7
7
2
2
2
2
5
5
10
9
7
7
9
9
5
5
6
5
7
7
6
6
6
6
5
4
8
8
12
10
5
4
4
4
7
7
4
4
6
6
5
5
14
12
8
8
9
9
3
2
8
7
14
10
4
4
9
8
7
4
6
6
5
5
17
17
2
2
6
6
8
8
14
8
5
5
9
8
3
3
6
6
11
11
2
2
12
10
8
7
3
3
2
2
3
3
6
5
3
3
7
7
4
4
8
8
10
10
10
7
10
8
2
2
7
5
7
7
6
5
2
1
8
6
10
9
14
13
2
2
7
5
10
10
9
8
2
2
11
11
12
12
7
7
5
5
2
2
8
8
6
5
11
8
7

13
11
7
7
12
11
2
2
2
2
8
8
8
7
6
6
6
6
5
5
5
5
2
1
2
2
2
2
3
3
9
7
9
9
10
8
3
3
9
9
3
3
4
4
8
7
4
4
6
5
8
8
4
4
5
5
8
8
7
7
9
7
7
7
10
10
7
7
10
9
11
9
9
8
15
13
13
10
9
6
12
12
13
10
12
12
7
7
8
8
7
7
3
3
3
3
2
2
7
7
12
9
8
7
7
7
2
2
6
6
3
3
11
11
2
2
15
15
5
4
6
6
2
2
7
6
4
4
8
8
4
4
8
7
7
7
11
9
15
10
9
9
13
10
10
9
3
3
17
15
10
9
14
10
6
5
9
7
2
2
6
6
2
2
11
9
8
8
6
5
3
2
10
6
3
3
4
4
13
10
7
7
4
4
5
5
9
8
5
5
6
5
4
4
11
10
3
3
6
6
11
7
9
9
2
2
5
5
5
5
3
3
3
3
5
5
9
7
12
11
2
2
6
6
5
4
11
9
12
10
2
2
4
4
2
2
9
8
7
7
7
6
10
9
5
5
5
5
7
2
7
7
3
3
7
7
2
2
9
9
8
7
10
10
10
10
6
5
2
2
5
5
3
3
8
8
12
12
5
5
4
4
15
14
3
3
3
3
3
3
9
8
7
7
2
2
4
4
4
4
3
3
6
6
3
3
2
2
5
4
10
10
5
5
5
4
6
6
2
2
4
4
5
5
14
12
9
9
7
6
2
1
8
8
7
7
2
2
6
6
10
10
4
4
3
3
12
11
7
7
3
3
5
5
3
3
9
9
2
2
8
8
13
11
4
4
9
8
14
14
2
2
14
14
10
8
3
3
6
6
5
5
3
3
2
2
6
6
8
7
2
2
2
2
7
7
16
12
6
6
4
4
11
9
3
2
6
4
9
9
9
9
7
6
2
2
2
2
14
12
2
2
2
2
2
2
11
10
2
2
14
12
11
11
6
6
3
3
2
2
3
3
2
2
9
8
11
10
13
11
9
9
10
9
11
10

12
10
8
8
8
8
13
11
5
4
6
5
3
3
3
3
10
8
5
5
14
14
8
8
6
6
4
4
12
9
3
3
2
2
2
2
16
11
17
14
13
13
12
12
6
6
11
9
6
6
6
5
2
2
2
2
2
2
2
2
11
11
10
10
4
4
2
2
22
15
2
2
12
12
6
6
6
6
3
3
13
11
2
2
11
10
8
8
5
5
6
6
3
3
6
6
6
6
2
2
3
3
6
6
12
8
7
6
14
12
13
12
9
7
5
5
11
8
5
5
2
2
5
5
3
3
5
5
7
7
3
3
4
4
15
13
8
8
9
8
4
3
9
9
10
9
3
3
2
2
12
11
7
6
10
10
2
2
16
12
10
9
9
8
7
6
15
11
10
10
7
6
11
11
2
2
8
8
9
9
12
10
6
6
6
6
8
8
10
8
9
9
15
9
8
6
15
13
2
2
9
9
2
2
9
9
2
2
6
5
6
5
9
8
5
5
9
9
9
8
9
9
4
3
2
2
13
12
12
11
3
3
11
10
4
4
7
7
5
5
10
9
9
9
8
8
5
4
11
9
7
6
7
6
6
6
10
9
3
3
7
7
3
3
6
5
7
6
14
12
13
13
5
4
2
2
2
2
7
6
2
2
4
4
2
2
2
2
9
9
11
9
4
4
17
15
2
2
9
8
2
2
2
2
5
4
12
12
10
10
5
5
12
12
10
10
7
6
12
11
11
11
2
2
6
6
5
5
12
9
2
2
16
11
10
10
7
7
11
9
3
3
11
11
16
13
7
6
12
11
5
5
9
9
11
10
6
6
6
6
12
11
9
9
4
4
5
5
14
11
12
9
16
14
11
9
9
7
8
7
2
2
8
8
7
7
9
8
3
3
10
10
13
10
11
9
14
14
3
3
4
4
8
7
12
11
2
2
4
4
6
5
10
7
7
6
8
7
2
2
9
9
15
14
6
6
2
2
8
7
14
14
16
8
7
7
7
7
10

In [64]:
random.choice([[1,2],[2,3]])

[1, 2]

In [36]:
for i in range(len(clusters)):
    print(clusters[i].address_set)

[<__main__.Address object at 0x7fbdb7fe6e48>, <__main__.Address object at 0x7fbdb51a9e48>]
[<__main__.Address object at 0x7fbdb7df75f8>, <__main__.Address object at 0x7fbdb6d9d5f8>, <__main__.Address object at 0x7fbdb51efe48>]
[<__main__.Address object at 0x7fbdb7732c18>, <__main__.Address object at 0x7fbdb5941908>, <__main__.Address object at 0x7fbdb5685cf8>]
[<__main__.Address object at 0x7fbdb8d98cf8>, <__main__.Address object at 0x7fbdb78fe278>, <__main__.Address object at 0x7fbdb6046dd8>, <__main__.Address object at 0x7fbdb5e51b38>]
[<__main__.Address object at 0x7fbdbbd40358>, <__main__.Address object at 0x7fbdb91fc978>, <__main__.Address object at 0x7fbdb66b9eb8>, <__main__.Address object at 0x7fbdb5512748>]
[<__main__.Address object at 0x7fbd98c09400>, <__main__.Address object at 0x7fbdb9297c18>, <__main__.Address object at 0x7fbdb9091828>, <__main__.Address object at 0x7fbdb5d460b8>, <__main__.Address object at 0x7fbdb5c80cf8>, <__main__.Address object at 0x7fbda2cac518>, <__m

[<__main__.Address object at 0x7fbdb1837048>, <__main__.Address object at 0x7fbdb9377668>, <__main__.Address object at 0x7fbdb1a94668>, <__main__.Address object at 0x7fbdb7260eb8>, <__main__.Address object at 0x7fbdb6a08eb8>, <__main__.Address object at 0x7fbdb6b8e908>, <__main__.Address object at 0x7fbdb729ef28>, <__main__.Address object at 0x7fbdb5bf6198>, <__main__.Address object at 0x7fbdb372cba8>, <__main__.Address object at 0x7fbdb38c0fd0>]
[<__main__.Address object at 0x7fbdb9377668>, <__main__.Address object at 0x7fbdb729ef28>, <__main__.Address object at 0x7fbdb7260eb8>, <__main__.Address object at 0x7fbdb6b8e908>, <__main__.Address object at 0x7fbdb6a08eb8>, <__main__.Address object at 0x7fbdb5bf6198>, <__main__.Address object at 0x7fbdb5bf6198>, <__main__.Address object at 0x7fbdb372cba8>, <__main__.Address object at 0x7fbdb38c0fd0>, <__main__.Address object at 0x7fbdb1a94668>, <__main__.Address object at 0x7fbdb1837048>]
[<__main__.Address object at 0x7fbdb8283c18>, <__main

[<__main__.Address object at 0x7fbdb90d1978>, <__main__.Address object at 0x7fbdb685d828>, <__main__.Address object at 0x7fbdb685d828>, <__main__.Address object at 0x7fbdb685d828>, <__main__.Address object at 0x7fbdb4da5828>, <__main__.Address object at 0x7fbdb0187400>]
[<__main__.Address object at 0x7fbdb4b54e48>, <__main__.Address object at 0x7fbdb4b54e48>, <__main__.Address object at 0x7fbdafa2d358>]
[<__main__.Address object at 0x7fbdbad3ca58>, <__main__.Address object at 0x7fbdb938e908>, <__main__.Address object at 0x7fbdb89d9278>, <__main__.Address object at 0x7fbdb7ac2d68>, <__main__.Address object at 0x7fbdb6a3d4a8>, <__main__.Address object at 0x7fbdb61a94a8>, <__main__.Address object at 0x7fbdb2ec5278>, <__main__.Address object at 0x7fbdaf193860>]
[<__main__.Address object at 0x7fbdb4664400>, <__main__.Address object at 0x7fbdb7750048>, <__main__.Address object at 0x7fbdb3462470>, <__main__.Address object at 0x7fbdb6c92cf8>]
[<__main__.Address object at 0x7fbdb7710ac8>, <__ma

[<__main__.Address object at 0x7fbda362ae10>, <__main__.Address object at 0x7fbd9c97cc50>, <__main__.Address object at 0x7fbdb19bc7b8>, <__main__.Address object at 0x7fbd9da472e8>]
[<__main__.Address object at 0x7fbdb3512898>, <__main__.Address object at 0x7fbdb3512898>, <__main__.Address object at 0x7fbdabf53dd8>]
[<__main__.Address object at 0x7fbdb8658438>, <__main__.Address object at 0x7fbdbf99a630>, <__main__.Address object at 0x7fbdaea37470>, <__main__.Address object at 0x7fbdbcf7c0b8>, <__main__.Address object at 0x7fbdaad67cf8>, <__main__.Address object at 0x7fbdcad91ef0>, <__main__.Address object at 0x7fbdb5acef28>, <__main__.Address object at 0x7fbdb8482b38>, <__main__.Address object at 0x7fbdb6929b38>, <__main__.Address object at 0x7fbdb2f8e198>]
[<__main__.Address object at 0x7fbdb4666128>, <__main__.Address object at 0x7fbdabdaeb38>, <__main__.Address object at 0x7fbdb08a8828>, <__main__.Address object at 0x7fbdc06f2438>]
[<__main__.Address object at 0x7fbdb7c32048>, <__ma

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [45]:
p = 0
s = 0
for t in pool:
    if t.type == "peel":
        p += 1
    elif t.type == "sweep":
        s += 1 
print(p)
print(s)

468714
46941


In [55]:
for t in match:
    print(t.to[1].id)

3846
44028
27092
39302
40354
30477
42096
35067
40106
6226
47547


IndexError: list index out of range

In [53]:
NODES[0]

In [77]:
a = [1,2,3,4,5,6,7,8,9,10]

In [84]:
b = range(1, 5)

In [85]:
a[b[0]:b[-1]]

[2, 3, 4]

In [98]:
ic = 0
oc = 0
for t in pool:
    for ts in t.sender:
        if NODES[0] == ts.address.Node:
            ic += 1
            break
    if NODES[0] in t.to:
        oc += 1
print(ic)
print(oc)

103
151
